In [1]:
import sys,time

import midi2audio
import transformers
from transformers import AutoModelForCausalLM, BertTokenizer, GPT2LMHeadModel

from IPython.display import Audio

from anticipation import ops
from anticipation.sample import generate
from anticipation.tokenize import extract_instruments
from anticipation.convert import events_to_midi,midi_to_events
from anticipation.visuals import visualize
from anticipation.config import *
from anticipation.vocab import *

import tqdm

c:\Users\phili\AppData\Local\Programs\Python\Python39\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
small_john_path = 'stanford-crfm/music-small-800k' 
john_model = AutoModelForCausalLM.from_pretrained(small_john_path)

# john_model.device("")

# our_model = GPT2LMHeadModel.from_pretrained("beat-goes-on/wiki-bert-tiny")
our_model = GPT2LMHeadModel.from_pretrained("beat-goes-on/HF_wiki_kmeans")

# our_model.device("")

# a MIDI synthesizer
fs = midi2audio.FluidSynth('word2house\8MBGMSFX.SF2')

# sem_tokenizer = BertTokenizer.from_pretrained("google-bert/bert-base-uncased", padding='max_length', max_length=64)

# the MIDI synthesis script
def synthesize(fs, tokens, filename):
    mid = events_to_midi(tokens)
    mid.save(f'{filename}.mid')
    fs.midi_to_audio(f'{filename}.mid', f'{filename}.wav')
    return f'{filename}.wav'

Some weights of the model checkpoint at stanford-crfm/music-small-800k were not used when initializing GPT2LMHeadModel: ['token_out_embeddings']
- This IS expected if you are initializing GPT2LMHeadModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing GPT2LMHeadModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [6]:
# Generate Unconditional John
length = 10
unconditional_tokens = generate(john_model, start_time=0, end_time=length, top_p=.98, debug=False)
Audio(synthesize(fs, unconditional_tokens, 'unconditional_default'))

 34%|███▎      | 337/1000 [05:38<11:06,  1.00s/it]


KeyboardInterrupt: 

In [6]:
"""
API functions for sampling from anticipatory infilling models.
"""

import math
import random
import torch
import torch.nn.functional as F

from tqdm import tqdm

from anticipation import ops
from anticipation.config import *
from anticipation.vocab import *


def safe_logits(logits, idx):
    logits[CONTROL_OFFSET:SPECIAL_OFFSET] = -float('inf') # don't generate controls
    logits[SPECIAL_OFFSET:] = -float('inf')               # don't generate special tokens

    # don't generate stuff in the wrong time slot
    if idx % 3 == 0:
        logits[DUR_OFFSET:DUR_OFFSET+MAX_DUR] = -float('inf')
        logits[NOTE_OFFSET:NOTE_OFFSET+MAX_NOTE] = -float('inf')
    elif idx % 3 == 1:
        logits[TIME_OFFSET:TIME_OFFSET+MAX_TIME] = -float('inf')
        logits[NOTE_OFFSET:NOTE_OFFSET+MAX_NOTE] = -float('inf')
    elif idx % 3 == 2:
        logits[TIME_OFFSET:TIME_OFFSET+MAX_TIME] = -float('inf')
        logits[DUR_OFFSET:DUR_OFFSET+MAX_DUR] = -float('inf')

    return logits


def nucleus(logits, top_p):
    # from HF implementation
    if top_p < 1.0:
        sorted_logits, sorted_indices = torch.sort(logits, descending=True)
        cumulative_probs = torch.cumsum(F.softmax(sorted_logits, dim=-1), dim=-1)

        # Remove tokens with cumulative probability above the threshold (token with 0 are kept)
        sorted_indices_to_remove = cumulative_probs > top_p

        # Shift the indices to the right to keep also the first token above the threshold
        sorted_indices_to_remove[..., 1:] = sorted_indices_to_remove[..., :-1].clone()
        sorted_indices_to_remove[..., 0] = 0

        # scatter sorted tensors to original indexing
        indices_to_remove = sorted_indices_to_remove.scatter(0, sorted_indices, sorted_indices_to_remove)
        logits[indices_to_remove] = -float("inf")

    return logits


def future_logits(logits, curtime):
    """ don't sample events in the past """
    if curtime > 0:
        logits[TIME_OFFSET:TIME_OFFSET+curtime] = -float('inf')

    return logits


def instr_logits(logits, full_history):
    """ don't sample more than 16 instruments """
    instrs = ops.get_instruments(full_history)
    if len(instrs) < 16:
        return logits
    # print(instrs)
    for instr in range(MAX_INSTR):
        if instr not in instrs:
            # print(instr)
            logits[NOTE_OFFSET+instr*MAX_PITCH:NOTE_OFFSET+(instr+1)*MAX_PITCH] = -float('inf')

    return logits


def our_add_token(model, z, tokens, top_p, current_time, debug=False):
    assert len(tokens) % 3 == 0

    history = tokens.copy()
    lookback = max(len(tokens) - 1017, 0)
    history = history[lookback:] # Markov window
    offset = ops.min_time(history, seconds=False)
    history[::3] = [tok - offset for tok in history[::3]] # relativize time in the history buffer

    new_token = []
    with torch.no_grad():
        for i in range(3):
            input_tokens = torch.tensor(z + history + new_token).unsqueeze(0).to(model.device)
            logits = model(input_tokens).logits[0,-1]

            # print(logits)
            idx = input_tokens.shape[1]-1
            logits = safe_logits(logits, idx)
            if i == 0:
                logits = future_logits(logits, current_time - offset)
            elif i == 2:
                logits = instr_logits(logits, tokens)
            logits = nucleus(logits, top_p)

            probs = F.softmax(logits, dim=-1)
            token = torch.multinomial(probs, 1)
            instrs = ops.get_instruments(tokens)
            if i == 2 and len(instrs.keys()) >= 16:
                # pitch = token % MAX_PITCH
                instr_probs = {}
                for instr in instrs:
                    instr_probs[probs[instr]] = instr
                token = instr_probs[max(instr_probs.keys())]*MAX_PITCH  + NOTE_OFFSET
            new_token.append(int(token))

    new_token[0] += offset # revert to full sequence timing
    if debug:
        print(f'  OFFSET = {offset}, LEN = {len(history)}, TIME = {tokens[::3][-5:]}')
    
    # print(new_token)
    return new_token


def our_generate(model, start_time, end_time, inputs=None, controls=None, top_p=1.0, debug=False, delta=DELTA*TIME_RESOLUTION, text_prompt=None, sem_tokenizer=None):
    if inputs is None:
        inputs = []

    if controls is None:
        controls = []

    start_time = int(TIME_RESOLUTION*start_time)
    end_time = int(TIME_RESOLUTION*end_time)

    # prompt is events up to start_time
    prompt = ops.pad(ops.clip(inputs, 0, start_time, clip_duration=False, seconds=False), start_time)

    # treat events beyond start_time as controls
    future = ops.clip(inputs, start_time+1, ops.max_time(inputs, seconds=False), clip_duration=False, seconds=False)
    if debug:
        print('Future')
        ops.print_tokens(future)

    # clip controls that preceed the sequence
    controls = ops.clip(controls, DELTA, ops.max_time(controls, seconds=False), clip_duration=False, seconds=False)

    if debug:
        print('Controls')
        ops.print_tokens(controls)

    # z = [ANTICIPATE] if len(controls) > 0 or len(future) > 0 or text_prompt == None else sem_tokenizer.encode(text_prompt)
    z = "" # FIND A CLUSTER
    if debug:
        print('AR Mode' if z[0] == AUTOREGRESS else 'AAR Mode')

    # interleave the controls with the events
    tokens, controls = ops.anticipate(prompt, ops.sort(controls + [CONTROL_OFFSET+token for token in future]))
    # tokens = prompt
    if debug:
        print('Prompt')
        ops.print_tokens(tokens)

    current_time = ops.max_time(prompt, seconds=False)
    if debug:
        print('Current time:', current_time)

    with tqdm(range(end_time-start_time)) as progress:
        if controls:
            atime, adur, anote = controls[0:3]
            anticipated_tokens = controls[3:]
            anticipated_time = atime - ATIME_OFFSET
        else:
            # nothing to anticipate
            anticipated_time = math.inf
        
        while True:
            while current_time >= anticipated_time - delta:
                tokens.extend([atime, adur, anote])
                if debug:
                    note = anote - ANOTE_OFFSET
                    instr = note//2**7
                    print('A', atime - ATIME_OFFSET, adur - ADUR_OFFSET, instr, note - (2**7)*instr)

                if len(anticipated_tokens) > 0:
                    atime, adur, anote = anticipated_tokens[0:3]
                    anticipated_tokens = anticipated_tokens[3:]
                    anticipated_time = atime - ATIME_OFFSET
                else:
                    # nothing more to anticipate
                    anticipated_time = math.inf
            new_token = our_add_token(model, z, tokens, top_p, max(start_time,current_time))
            new_time = new_token[0] - TIME_OFFSET
            # We generated one note!
            # (note_start, duration, note_value)
            # new_time = current_time + random.randint(1, 5)

            # Check to make sure not too long. Yup.
            # new_token[1] = new_token[1] % MAX_DUR + DUR_OFFSET
            
            # new_token[2] = new_token[2] % MAX_NOTE + NOTE_OFFSET


            
            if new_time >= end_time:
                break

            if debug:
                new_note = new_token[2] - NOTE_OFFSET
                new_instr = new_note//2**7
                new_pitch = new_note - (2**7)*new_instr
                print('C', new_time, new_token[1] - DUR_OFFSET, new_instr, new_pitch)

            tokens.extend(new_token)
            dt = new_time - current_time
            assert dt >= 0
            current_time = new_time
            progress.update(dt)

    events, _ = ops.split(tokens)
    return ops.sort(ops.unpad(events) + future)

def our_generate_ar(model, start_time, end_time, inputs=None, controls=None, top_p=1.0, debug=False, delta=DELTA*TIME_RESOLUTION, text_prompt=None, sem_tokenizer=None):
    if inputs is None:
        inputs = []

    if controls is None:
        controls = []
    else:
        # treat controls as ordinary tokens
        controls = [token-CONTROL_OFFSET for token in controls]

    start_time = int(TIME_RESOLUTION*start_time)
    end_time = int(TIME_RESOLUTION*end_time)

    inputs = ops.sort(inputs + controls)

    # prompt is events up to start_time
    prompt = ops.pad(ops.clip(inputs, 0, start_time, clip_duration=False, seconds=False), start_time)
    if debug:
        print('Prompt')
        ops.print_tokens(prompt)

    # treat events beyond start_time as controls
    controls = ops.clip(inputs, start_time+1, ops.max_time(inputs, seconds=False), clip_duration=False, seconds=False)
    if debug:
        print('Future')
        ops.print_tokens(controls)

    z = sem_tokenizer.encode(text_prompt)
    if debug:
        print('AR Mode')

    current_time = ops.max_time(prompt, seconds=False)
    if debug:
        print('Current time:', current_time)

    tokens = prompt
    with tqdm(range(end_time-start_time)) as progress:
        if controls:
            atime, adur, anote = controls[0:3]
            anticipated_tokens = controls[3:]
            anticipated_time = atime - TIME_OFFSET
        else:
            # nothing to anticipate
            anticipated_time = math.inf
        
        while True:
            new_token = our_add_token(model, z, tokens, top_p, max(start_time,current_time))
            # new_time = new_token[0] - TIME_OFFSET
            new_time = current_time + 5
            if new_time >= end_time:
                print(tokens)
                normed_tokens = [TIME_OFFSET]
                normed_tokens.extend(tokens[1:3])
                instrs = set()
                instrs.add((tokens[2] - NOTE_OFFSET) / 2 ** 7)
                for i in range(3, len(tokens), 3):
                    note = tokens[i + 2] - NOTE_OFFSET
                    instr = note//2**7
                    if instr in instrs or len(instrs) < 16:
                        normed_tokens.extend([normed_tokens[-3] + 1, tokens[i + 1], tokens[i + 2]])
                        instrs.add(instr)
                tokens = normed_tokens
                break

            dt = new_time - current_time
            assert dt >= 0
            current_time = new_time

            # backfill anything that should have come before the new token
            while current_time >= anticipated_time:
                tokens.extend([atime, adur, anote])
                if debug:
                    note = anote - NOTE_OFFSET
                    instr = note//2**7
                    print('A', atime - TIME_OFFSET, adur - DUR_OFFSET, instr, note - (2**7)*instr)

                if len(anticipated_tokens) > 0:
                    atime, adur, anote = anticipated_tokens[0:3]
                    anticipated_tokens = anticipated_tokens[3:]
                    anticipated_time = atime - TIME_OFFSET
                else:
                    # nothing more to anticipate
                    anticipated_time = math.inf

            if debug:
                new_note = new_token[2] - NOTE_OFFSET
                new_instr = new_note//2**7
                new_pitch = new_note - (2**7)*new_instr
                print('C', new_time, new_token[1] - DUR_OFFSET, new_instr, new_pitch)

            tokens.extend(new_token)
            progress.update(dt)

    if anticipated_time != math.inf:
        tokens.extend([atime, adur, anote])

    return ops.sort(ops.unpad(tokens) + controls)


In [13]:


from cluster_inference import get_cluster

def generate_kmeans(model, start_time, end_time, textPrompt=None, inputs=None, controls=None, top_p=1.0, debug=False, delta=DELTA*TIME_RESOLUTION):
    if inputs is None:
        inputs = []

    if controls is None:
        controls = []
    else:
        # treat controls as ordinary tokens
        controls = [token-CONTROL_OFFSET for token in controls]

    start_time = int(TIME_RESOLUTION*start_time)
    end_time = int(TIME_RESOLUTION*end_time)

    inputs = ops.sort(inputs + controls)

    # prompt is events up to start_time
    prompt = ops.pad(ops.clip(inputs, 0, start_time, clip_duration=False, seconds=False), start_time)
    if debug:
        print('Prompt')
        ops.print_tokens(prompt)

    # treat events beyond start_time as controls
    controls = ops.clip(inputs, start_time+1, ops.max_time(inputs, seconds=False), clip_duration=False, seconds=False)
    if debug:
        print('Future')
        ops.print_tokens(controls)

    z = [get_cluster(textPrompt)] if textPrompt != None else [AUTOREGRESS]
    if debug:
        print('AR Mode')

    current_time = ops.max_time(prompt, seconds=False)
    if debug:
        print('Current time:', current_time)

    tokens = prompt
    with tqdm(range(end_time-start_time)) as progress:
        if controls:
            atime, adur, anote = controls[0:3]
            anticipated_tokens = controls[3:]
            anticipated_time = atime - TIME_OFFSET
        else:
            # nothing to anticipate
            anticipated_time = math.inf

        while True:
            new_token = add_token(model, z, tokens, top_p, max(start_time,current_time))
            new_time = new_token[0] - TIME_OFFSET
            if new_time >= end_time:
                break

            dt = new_time - current_time
            assert dt >= 0
            current_time = new_time

            # backfill anything that should have come before the new token
            while current_time >= anticipated_time:
                tokens.extend([atime, adur, anote])
                if debug:
                    note = anote - NOTE_OFFSET
                    instr = note//2**7
                    print('A', atime - TIME_OFFSET, adur - DUR_OFFSET, instr, note - (2**7)*instr)

                if len(anticipated_tokens) > 0:
                    atime, adur, anote = anticipated_tokens[0:3]
                    anticipated_tokens = anticipated_tokens[3:]
                    anticipated_time = atime - TIME_OFFSET
                else:
                    # nothing more to anticipate
                    anticipated_time = math.inf

            if debug:
                new_note = new_token[2] - NOTE_OFFSET
                new_instr = new_note//2**7
                new_pitch = new_note - (2**7)*new_instr
                print('C', new_time, new_token[1] - DUR_OFFSET, new_instr, new_pitch)

            tokens.extend(new_token)
            progress.update(dt)

    if anticipated_time != math.inf:
        tokens.extend([atime, adur, anote])

    return ops.sort(ops.unpad(tokens) + controls)


UnpicklingError: pickle stream refers to out-of-band data but no *buffers* argument was given

In [ ]:
# Generate Unconditional Our Model
length = 1
# unconditional_tokens = our_generate(our_model, debug=False, start_time=0, end_time=length, top_p=.98, text_prompt="make me a silly song for my friends", sem_tokenizer=sem_tokenizer)
unconditional_tokens = generate_kmeans(our_model, debug=False, start_time=0, end_time=length, top_p=.98, text_prompt="make me a silly song for my friends")
print(unconditional_tokens)
Audio(synthesize(fs, unconditional_tokens, "unconditional_new_kmeans"))

 95%|█████████▌| 95/100 [00:02<00:00, 33.39it/s]

[1050, 10022, 14255, 2098, 10022, 21199, 1093, 10230, 20274, 1150, 10107, 14745, 1150, 10716, 17460, 2582, 10043, 15385, 5608, 10011, 17221, 3507, 10022, 14264, 1150, 10508, 12498, 1108, 10011, 14520, 3590, 10013, 14513, 1109, 10613, 21334, 5976, 10754, 27426, 2894, 10015, 27459, 2106, 10022, 14264, 2073, 10067, 14252, 1111, 10125, 14503, 3477, 10006, 14757, 1222, 10029, 14252]
[0, 10022, 14255, 1, 10022, 21199, 2, 10230, 20274, 3, 10107, 14745, 4, 10716, 17460, 5, 10043, 15385, 6, 10011, 17221, 7, 10022, 14264, 8, 10508, 12498, 9, 10011, 14520, 10, 10013, 14513, 11, 10613, 21334, 12, 10754, 27426, 13, 10015, 27459, 14, 10022, 14264, 15, 10067, 14252, 16, 10125, 14503, 17, 10006, 14757, 18, 10029, 14252]


NameError: name 'generate_kmeans' is not defined

In [169]:
import os

filelist = os.listdir('dataset/wiki_default_bert_tokenized/e')
filelist = [f for f in filelist if f[-3:] == 'mid']

john_ces = [-44495, -40554, -630642, 4389, -311, -1911, 4998, 11316, 22346, -70455, 25300, 295567, -108768, -118763, 20435, 138516, 218962, -20520, 4903, -836, -381803, 1725, -209467, -17747, -27925, 132629, -101275, -92598, 83662, 10812]
our_ces = [-61020, -112529, -517578, -57357, 10962, -297973, -36261, -262557, 29668, -112276, -76389, 431861, -28865, -318865, -121997, 27076, 76858, -129268, -175753, -205177, -488923, -178867, -272198, -127906, -219449, 141812, -200551, -204597, 169457, 1107]
# Cross Entropy Script
for i in tqdm(range(40, 60)):
    if i % 10 == 0:
        print(john_ces)
        print(our_ces)
    events = midi_to_events(f'dataset/wiki_default_bert_tokenized/e/{filelist[i]}')
    segment = ops.clip(events, 15, 20)
    segment = ops.translate(segment, -ops.min_time(segment, seconds=False))
    history = ops.clip(segment, 0, 4, clip_duration=False)
    inpainted_john = generate(john_model, 4, 5, inputs=history, top_p=.95)
    inpainted_our = our_generate(our_model, 4, 5, inputs=history, top_p=.95)
    ce_john = 0
    ce_ours = 0
    for i in range(min(len(inpainted_john), len(events))):
        ce_john += (events[i] - inpainted_john[i])
    for i in range(min(len(inpainted_our), len(events))):
        ce_ours += (events[i] - inpainted_our[i])
    john_ces.append(ce_john)
    our_ces.append(ce_ours)

print(john_ces)
print(our_ces)

print(f"Avg John CEs: {sum(john_ces) / len(john_ces)}")
print(f"Avg Our CEs: {sum(our_ces) / len(our_ces)}")

  0%|          | 0/20 [00:00<?, ?it/s]

[-44495, -40554, -630642, 4389, -311, -1911, 4998, 11316, 22346, -70455, 25300, 295567, -108768, -118763, 20435, 138516, 218962, -20520, 4903, -836, -381803, 1725, -209467, -17747, -27925, 132629, -101275, -92598, 83662, 10812]
[-61020, -112529, -517578, -57357, 10962, -297973, -36261, -262557, 29668, -112276, -76389, 431861, -28865, -318865, -121997, 27076, 76858, -129268, -175753, -205177, -488923, -178867, -272198, -127906, -219449, 141812, -200551, -204597, 169457, 1107]


 86%|████████▌ | 86/100 [00:00<00:00, 128.07it/s]
132it [00:07, 17.97it/s]
199it [00:20,  9.67it/s]0:08<02:36,  8.21s/it]
199it [00:11, 17.25it/s]
113it [00:12,  9.29it/s]0:40<06:41, 22.29s/it]
114it [00:12,  8.79it/s]
 97%|█████████▋| 97/100 [00:48<00:01,  1.98it/s]
101it [00:25,  4.02it/s]
101it [00:07, 13.02it/s]2:35<09:57, 39.82s/it]
112it [00:11, 10.05it/s]
 56%|█████▌    | 56/100 [00:02<00:02, 19.61it/s]
105it [00:06, 16.60it/s]
 94%|█████████▍| 94/100 [00:11<00:00,  8.26it/s]
103it [00:11,  8.77it/s]
 95%|█████████▌| 95/100 [00:48<00:02,  1.96it/s]
104it [00:17,  6.10it/s]
 65%|██████▌   | 65/100 [00:04<00:02, 14.76it/s]
111it [00:10, 10.76it/s]
 50%|█████     | 10/20 [04:48<05:06, 30.62s/it]

[-44495, -40554, -630642, 4389, -311, -1911, 4998, 11316, 22346, -70455, 25300, 295567, -108768, -118763, 20435, 138516, 218962, -20520, 4903, -836, -381803, 1725, -209467, -17747, -27925, 132629, -101275, -92598, 83662, 10812, 1019, -419348, -2074, 32, -89194, 10612, 573, -214662, -184923, 53261]
[-61020, -112529, -517578, -57357, 10962, -297973, -36261, -262557, 29668, -112276, -76389, 431861, -28865, -318865, -121997, 27076, 76858, -129268, -175753, -205177, -488923, -178867, -272198, -127906, -219449, 141812, -200551, -204597, 169457, 1107, 57347, -431225, -168760, -188187, -163599, -174270, -162944, -162341, -258585, -49442]


 42%|████▏     | 42/100 [00:00<00:01, 55.63it/s] 
123it [00:08, 14.17it/s]
 96%|█████████▌| 96/100 [00:05<00:00, 17.71it/s]
104it [00:28,  3.63it/s]05:38<02:14, 19.26s/it]
 93%|█████████▎| 93/100 [00:15<00:01,  6.03it/s]
107it [00:21,  5.08it/s]
 85%|████████▌ | 85/100 [00:02<00:00, 39.63it/s]
113it [00:09, 12.39it/s]
103it [00:03, 25.97it/s]07:14<01:39, 24.90s/it]
109it [00:08, 13.53it/s]
 93%|█████████▎| 93/100 [00:15<00:01,  5.97it/s]
105it [00:12,  8.41it/s]
 80%|████████  | 80/100 [00:03<00:00, 25.86it/s]
106it [00:07, 13.50it/s]
 96%|█████████▌| 96/100 [00:40<00:01,  2.38it/s]
101it [00:22,  4.51it/s]
100%|██████████| 20/20 [09:10<00:00, 27.52s/it]

[-44495, -40554, -630642, 4389, -311, -1911, 4998, 11316, 22346, -70455, 25300, 295567, -108768, -118763, 20435, 138516, 218962, -20520, 4903, -836, -381803, 1725, -209467, -17747, -27925, 132629, -101275, -92598, 83662, 10812, 1019, -419348, -2074, 32, -89194, 10612, 573, -214662, -184923, 53261, 147661, 70, 1204, 81610, 42063, 18878, 146474, -246145, 14787, 184423]
[-61020, -112529, -517578, -57357, 10962, -297973, -36261, -262557, 29668, -112276, -76389, 431861, -28865, -318865, -121997, 27076, 76858, -129268, -175753, -205177, -488923, -178867, -272198, -127906, -219449, 141812, -200551, -204597, 169457, 1107, 57347, -431225, -168760, -188187, -163599, -174270, -162944, -162341, -258585, -49442, 119116, -93920, 23043, 62793, -9881, -284909, -2576, -509541, -236827, 112475]
Avg John CEs: -26923.78
Avg Our CEs: -116795.76


30